# Pre-requisites

## Why TEI
There are 2 **unsung** challenges with RAG at scale:
1. Getting the embeddings efficiently
1. Efficient ingestion into the vector DB

The issue with `1.` is that there are techniques but they are not widely *applied*. TEI solves a number of aspects:
- Token Based Dynamic Batching
- Using latest optimizations (Flash Attention, Candle and cuBLASLt)
- Fast loading with safetensors

The issue with `2.` is that it takes a bit of planning. We wont go much into that side of things here though.

## Start TEI
Run [TEI](https://github.com/huggingface/text-embeddings-inference#docker), I have this running in a nvidia-docker container, but you can install as you like. Note that I ran this in a different terminal for monitoring and seperation. 

Note that as its running, its always going to pull the latest. Its at a very early stage at the time of writing. 

I chose the smaller [BAAI/bge-base-en-v1.5](https://huggingface.co/BAAI/bge-base-en-v1.5) instead of the large. Its just as good on [mteb/leaderboard](https://huggingface.co/spaces/mteb/leaderboard) but its faster and smaller. TEI is fast, but this will make our life easier for storage and retrieval.

I use the `revision=refs/pr/1` because this has the pull request with [safetensors](https://github.com/huggingface/safetensors) which is required by TEI. Check out the [pull request](https://huggingface.co/BAAI/bge-base-en-v1.5/discussions/1) if you want to use a different embedding model and it doesnt have safetensors.

In [1]:
%%bash

# volume=$PWD/data
# model=BAAI/bge-base-en-v1.5
# revision=refs/pr/1
# docker run \
#     --gpus all \
#     -p 8080:80 \
#     -v $volume:/data \
#     --pull always \
#     ghcr.io/huggingface/text-embeddings-inference:latest \
#     --model-id $model \
#     --revision $revision \
#     --pooling cls \
#     --max-batch-tokens 65536

## Test Endpoint

In [2]:
%%bash

response_code=$(curl -s -o /dev/null -w "%{http_code}" 127.0.0.1:8080/embed \
    -X POST \
    -d '{"inputs":"What is Deep Learning?"}' \
    -H 'Content-Type: application/json')

if [ "$response_code" -eq 200 ]; then
    echo "passed"
else
    echo "failed"
fi

passed


# Imports

In [3]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

In [4]:
import asyncio
from pathlib import Path
import pickle

import aiohttp
from tqdm.notebook import tqdm

In [5]:
proj_dir = Path.cwd().parent
print(proj_dir)

/home/ec2-user/RAGDemo


# Config

I'm putting the documents in pickle files. The compression is nice, though its important to note pickles are known to be a security risk.

In [6]:
file_in = proj_dir / 'data/processed/simple_wiki_processed.pkl'
file_out = proj_dir / 'data/processed/simple_wiki_embeddings.pkl'

# Setup
Read in our list of documents and convert them to dictionaries for processing.

In [7]:
%%time
with open(file_in, 'rb') as handle:
    documents = pickle.load(handle)

documents = [document.to_dict() for document in documents]

CPU times: user 6.24 s, sys: 928 ms, total: 7.17 s
Wall time: 6.61 s


# Embed
## Strategy
TEI allows multiple concurrent requests, so its important that we dont waste the potential we have. I used the default `max-concurrent-requests` value of `512`, so I want to use that many `MAX_WORKERS`.

Im using an `async` way of making requests that uses `aiohttp` as well as a nice progress bar. 

In [8]:
# Constants
ENDPOINT = "http://127.0.0.1:8080/embed"
HEADERS = {'Content-Type': 'application/json'}
MAX_WORKERS = 512

Note that Im using `'truncate':True` as even with our `350` word split earlier, there are always exceptions. Its important that as this scales we have as few issues as possible when embedding. 

In [9]:
async def fetch(session, url, document):
    payload = {"inputs": [document["content"]], 'truncate':True}
    async with session.post(url, json=payload) as response:
        if response.status == 200:
            resp_json = await response.json()
            # Assuming the server's response contains an 'embedding' field
            document["embedding"] = resp_json[0]
        else:
            print(f"Error {response.status}: {await response.text()}")
            # Handle error appropriately if needed

async def main(documents):
    async with aiohttp.ClientSession(headers=HEADERS) as session:
        tasks = [fetch(session, ENDPOINT, doc) for doc in documents]
        await asyncio.gather(*tasks)

In [10]:
%%time
# Create a list of async tasks
tasks = [main(documents[i:i+MAX_WORKERS]) for i in range(0, len(documents), MAX_WORKERS)]

# Add a progress bar for visual feedback and run tasks
for task in tqdm(tasks, desc="Processing documents"):
    await task

Processing documents:   0%|          | 0/526 [00:00<?, ?it/s]

Lets double check that we got all the embeddings we expected!

In [11]:
count = 0
for document in documents:
    if len(document['embedding']) == 768:
        count += 1
count
len(documents)

268980

268980

Great, we can see that they match.

Let's write our embeddings to file

In [12]:
%%time
with open(file_out, 'wb') as handle:
    pickle.dump(documents, handle, protocol=pickle.HIGHEST_PROTOCOL)

CPU times: user 5.68 s, sys: 640 ms, total: 6.32 s
Wall time: 14.1 s


# Next Steps
We need to import this into a vector db. 